In [15]:
import pandas as pd
import pymysql as msql

In [ ]:
df = pd.read_csv(r'C:\Users\celds\Desktop\Vish.csv', nrows=10)

In [3]:
df.head(5)

Company  Order Status Product Number  Order Number Ordered Date  \
0       70           NaN       12MIFITD     1989635.0     7/1/2021   
1       70           NaN      NTEX14921     1989635.0     7/1/2021   
2       70           NaN      12MIFITDU     1989635.0     7/1/2021   
3       70           NaN  NTEX14921K12F     1989635.0     7/1/2021   
4       70           NaN          UTS4C     1989635.0     7/1/2021   

    Warehouse  Quantity    Value  Customer Number Quantity UOM  ...  \
0          LO         1     0.00         10000026       Eaches  ...   
1          NJ         1  1745.00         10000026       Eaches  ...   
2          LO         1   299.00         10000026       Eaches  ...   
3  Back Order         0     0.00         10000026       Eaches  ...   
4          LO         1   179.95         10000026       Eaches  ...   

  Origin Site ID Shipped Date          Segment  \
0            NaN     7/1/2021  Direct Response   
1            NaN     7/1/2021  Direct Response   
2            NaN     7/1/2021  Direct Response   
3            NaN     7/1/2021  Direct Response   
4            NaN     7/1/2021  Direct Response   

              Product Description  Product Class Product Brand  \
0           IFIT,COACH,12MO,MULTI            FIF          IFIT   
1      EB,NT COMMERCIAL R 35 BIKE            FEB   NORDICTRACK   
2  IFIT,MEMBRSHIP,2ND YEAR UPSELL            FIF          IFIT   
3                   NTEX14921K12F            NaN   NORDICTRACK   
4                           UTS4C            NaN           NaN   

   Product Category  Product Line Product Master Product Line SIOP FLASH GROUP  
0              IFIT                         IFIT              IFIT         NaN  
1              BIKE                         BIKE              BIKE         NaN  
2              IFIT                         IFIT              IFIT         NaN  
3              BIKE                         BIKE              BIKE         NaN  
4               UTS                          UTS               UTS         NaN  

[5 rows x 32 columns]

In [4]:
df.columns

Index(['Company', 'Order Status', 'Product Number', 'Order Number',
       'Ordered Date', 'Warehouse', 'Quantity', 'Value', 'Customer Number',
       'Quantity UOM', 'Status', 'Channel', 'Currency of Transactions',
       'Selling Price', 'Order Line ID', 'Order Entry Date',
       'Quantity Shipped', 'Customer Group Number', 'Region', 'Delivery Date',
       'Transaction Type', 'Planned Ship Date', 'Origin Site ID',
       'Shipped Date', 'Segment', 'Product Description', 'Product Class',
       'Product Brand', 'Product Category', 'Product Line Product Master',
       'Product Line SIOP', 'FLASH GROUP'],
      dtype='object')

In [8]:
code_map = {'Product Number':'PN0000', 'Product Category':'PCT0000', 'Product Class':'PC0000' , 'Product Brand':'PB0000', 'Product Line Product Master': 'PM0000', 'Warehouse': 'WH0000', 
          'Product Line SIOP': 'PLS0001', 'FLASH GROUP': 'FG0000'}

for key, value in code_map.items():

  new_col = key+ "_mapping"    
  df_map = pd.DataFrame(df[key].unique(), columns=[key])
  df_map[new_col] = 0
  for idx, row in df_map.iterrows():
    if row[0] == df_map.iloc[idx,0]:
      df_map.iloc[idx,1] = value+str(idx+1)
  df = pd.merge(df, df_map, on= [key], how ='left')

In [6]:
# df_map = pd.DataFrame(df['Product Brand'].unique(), columns=['Product Brand'])
# df_map['Prod_Brand_Mapping'] = 0
# for idx, value in df_map.iterrows():
#     if value[0] == df_map.iloc[idx,0]:
#             df_map.iloc[idx,1] = "PB0000"+str(idx+1)
# df = pd.merge(df, df_map, on= ['Product Brand'], how ='left')

In [14]:
df.head()

Company  Order Status Product Number  Order Number Ordered Date  \
0       70           NaN       12MIFITD     1989635.0     7/1/2021   
1       70           NaN      NTEX14921     1989635.0     7/1/2021   
2       70           NaN      12MIFITDU     1989635.0     7/1/2021   
3       70           NaN  NTEX14921K12F     1989635.0     7/1/2021   
4       70           NaN          UTS4C     1989635.0     7/1/2021   

    Warehouse  Quantity    Value  Customer Number Quantity UOM  ...  \
0          LO         1     0.00         10000026       Eaches  ...   
1          NJ         1  1745.00         10000026       Eaches  ...   
2          LO         1   299.00         10000026       Eaches  ...   
3  Back Order         0     0.00         10000026       Eaches  ...   
4          LO         1   179.95         10000026       Eaches  ...   

  Product Line Product Master_mapping_x Warehouse_mapping_x  \
0                               PM00001             WH00001   
1                               PM00002             WH00002   
2                               PM00001             WH00001   
3                               PM00002             WH00003   
4                               PM00003             WH00001   

  Product Number_mapping_y  Product Category_mapping_y  \
0                  PN00001                    PCT00001   
1                  PN00002                    PCT00002   
2                  PN00003                    PCT00001   
3                  PN00004                    PCT00002   
4                  PN00005                    PCT00003   

   Product Class_mapping_y Product Brand_mapping_y  \
0                  PC00001                 PB00001   
1                  PC00002                 PB00002   
2                  PC00001                 PB00001   
3                        0                 PB00002   
4                        0                       0   

   Product Line Product Master_mapping_y  Warehouse_mapping_y  \
0                                PM00001              WH00001   
1                                PM00002              WH00002   
2                                PM00001              WH00001   
3                                PM00002              WH00003   
4                                PM00003              WH00001   

  Product Line SIOP_mapping FLASH GROUP_mapping  
0                  PLS00011                   0  
1                  PLS00012                   0  
2                  PLS00011                   0  
3                  PLS00012                   0  
4                  PLS00013                   0  

[5 rows x 46 columns]

In [18]:

def db_connection():
    cnx = msql.connect(user='root', password='Mechanical', host= 'localhost', port=3306, database = 'test', autocommit=True)
    cursor = cnx.cursor()
    return (cnx, cursor)

In [23]:
for i in df.iterrows():
    print(tuple(i))

qry = """INSERT INTO test.transportation (COMPANY, ORDER_STATUS, PRODUCT_NUMBER,  ORDER_NUMBER, ORDERED_DATE, WAREHOUSE, QUANTITY, VALUE,  CUSTOMER_NUMBER, QUANTITY_UOM, STATUS, CHANNEL, CURRENCY_OF_TRANSACTIONS, 
        SELLING_PRICE, ORDER_LINE_ID, ORDER_ENTRY_DATE, QUANTITY_SHIPPED, CUSTOMER_GROUP_NUMBER, REGION, DELIVERY_DATE, TRANSACTION_TYPE, PLANNED_SHIP_DATE, ORIGIN_SITE_ID, SHIPPED_DATE, SEGMENT, PRODUCT_DESCRIPTION,
        PRODUCT_CLASS, PRODUCT_BRAND, PRODUCT_CATEGORY, PRODUCT_LINE_PRODUCT_MASTER, PRODUCT_LINE_SIOP, FLASH_GROUP ) VALUES """ + str(tuple(db_row)) +";"


(0, Company                                                     70
Order Status                                               NaN
Product Number                                        12MIFITD
Order Number                                       1.98964e+06
Ordered Date                                          7/1/2021
Warehouse                                                   LO
Quantity                                                     1
Value                                                        0
Customer Number                                       10000026
Quantity UOM                                            Eaches
Status                                               Completed
Channel                                                    DTC
Currency of Transactions                               Dollars
Selling Price                                                0
Order Line ID                                                3
Order Entry Date                                   

In [ ]:
cnx, cursor = db_connection()
cursor.execute(qry)
# cnx.close()